In [1]:
##modules
#%matplotlib widget
#%matplotlib inline
#
#%matplotlib qt
import mne
import numpy as np
import matplotlib
# Establecer un backend interactivo, como 'Qt5Agg', 'GTK3Agg', etc.
# Esto depende de los backends disponibles en tu sistema.

import matplotlib.pyplot as plt

matplotlib.use('TkAgg')  # Asegúrate de que este backend está instalado.

import pandas as pd 
import os
import sys

from mne.preprocessing import ICA, corrmap, create_ecg_epochs, create_eog_epochs

from os.path import join as pathjoin
from time import time

from pathlib import Path

from autoreject import AutoReject

# aplicar la acf EN epochs

from statsmodels.tsa.stattools import acf
import numpy as np

import pandas as pd

In [2]:
# Variables path
layer_script = "block"

#process=""
disco="g"

subj = "S01"

#subj = sys.argv[1] ## name of participant list

# Carpeta general
datadir = Path(f"{disco}:\\PROYECTO_SELF")

# #carpetas generales de datos
brain_vision_dir = datadir /"Data_self"/"Export_acw_Brain_Vision"
fif_data = datadir /"Data_self"/ "fif_data" 


#carpeta analysis
output_analysis= datadir / "output_analysis"

acw_analysis_path = output_analysis / "acw"
acw_analysis_path.mkdir(parents=True, exist_ok=True)

# # Carpeta de preprocesado
# output_preproc = datadir / "output_preproc"

# preproc_path = output_preproc / f"preproc_{layer_script}"
# preproc_path.mkdir(parents=True, exist_ok=True)
 
# # Carpeta de epocas "sucias"
# epochs_path = preproc_path / f"epochs_{layer_script}"
# epochs_path.mkdir(parents=True, exist_ok=True) 

# # Carpeta de ICA
# ICA_path = preproc_path / f"ICA_{layer_script}"
# ICA_path.mkdir(parents=True, exist_ok=True)

# # Épocas limpias
# epochs_clean_path = preproc_path / f"epochs_clean_{layer_script}"
# epochs_clean_path.mkdir(parents=True, exist_ok=True)

# #epocas epochs
# epochs_path = Path(preproc_path) / f"epochs_{layer_script}"
# epochs_path.mkdir(parents=True, exist_ok=True)
 

# # Definir la carpeta de output_source antes de usarla
# output_source = Path(r"g:\MOUS_204\output_source")

# source_path = output_source / f"source_{layer_script}"
# source_path.mkdir(parents=True, exist_ok=True)

# #raw_hsp es el raw con fiducials cargados
# raw_hsp_path = source_path / f"raw_hsp"
# raw_hsp_path.mkdir(parents=True, exist_ok=True)

# # Carpeta de forward solution
# fwd_path = source_path / f"fwd"
# fwd_path.mkdir(parents=True, exist_ok=True)

# # Carpeta de inverse solution
# inverse_path = source_path / f"inverse"
# inverse_path.mkdir(parents=True, exist_ok=True)


# mne.utils.set_config('SUBJECTS_DIR', r'\\wsl$\Ubuntu-20.04\usr\local\freesurfer\subjects', set_env=True)


In [3]:

#epochs
combinaciones = ["S1 - S4","S1 - S5", "S2 - S4", "S2 - S5", "S3 - S4", "S3 - S5"]

combinacion= combinaciones[1]

# Obtener todos los archivos y carpetas dentro de la ruta
subjects = list(fif_data.iterdir())

# Filtrar solo los nombres de sujetos (removiendo "_epochs")
subject_names = [subject.stem.replace("_epochs", "") for subject in subjects]

subj=subject_names[0]
subj


# # epochs_zinnen_path = epochs_clean_path / f"{subj}_epochs_zinnen_{type_script}"
# # epochs_path = epochs_clean_path / f"{subj}_epochs_{type_script}"

path_epochs= fif_data / f"{subj}_epochs" / f"{subj}_{combinacion}-epo.fif"

epochs = mne.read_epochs(path_epochs) 





Reading g:\PROYECTO_SELF\Data_self\fif_data\S01_epochs\S01_S1 - S5-epo.fif ...
    Found the data of interest:
        t =       0.00 ...    9198.00 ms
        0 CTF compensation matrices available
Not setting metadata
21 matching events found
No baseline correction applied
0 projection items activated


In [ ]:
# aplicar la acf EN epochs

from statsmodels.tsa.stattools import acf
import numpy as np

import pandas as pd

def acf_epochs(epochs,condition,num_conditions ,adjusted=False,fft=True,alpha=None, bartlett_confint=True, missing="none", isplot=False): 
    
    #import epochs object and get data ONLY ON MEG DATA
    data_epochs=epochs.copy().pick("eeg").get_data()

    #get duration
    duration= epochs.tmax - epochs.tmin
    #get sample frequency
    sfreq= epochs.info['sfreq']
    #get lags
    lags=duration*sfreq


    #list to store the values of acf, acw_50,acw_0 for each epoch for each sensor for each EPOCH
    acf_elect_all_epoch_all = []
    acf_mean_elect_all_epoch_all=[]

    #conjunto de todos los valores de ACW_0-ACW_50 para cada sensor en cada epoca
    acw_50_elect_all_epoch_all = []
    acw_0_elect_all_epoch_all = []


    #for each epoch
      
    for j in range(0,len(data_epochs)):
        #take data for each epoch
        data_epoch=data_epochs[j]

        #list to store the values of acf, acw_50,acw_0 for each SENSOR for each EPOCH

        acf_elect_all_epoch = []
        
        acf_mean_elect_all_epoch = []

        acw_50_elect_all_epoch = []
        acw_0_elect_all_epoch = []

    


        #calculus of value  for EACH SENSOR
        for i in range(0,len(data_epoch)):
            #lags se puede dejar por defecto porque te cogelos valores
            #hasta los que tiene sentido calcularlo, aunque yo voy a calcularlo para todos los lags
            #calculo de acf de sensor
            #alfa lo dejo endefault que es la confianza del 95% 

            acf_elect_epoch, qstat_vals_elect_epoch, pvals_elect_epoch = acf(
                data_epoch[i],
                adjusted=adjusted,
                fft=fft,
                qstat=True,
                nlags=lags,
                alpha=alpha,
                bartlett_confint=bartlett_confint,
                missing=missing
            )

            #conjunto de valores de acf en un electrodo en una epoca
            acf_elect_all_epoch.append(acf_elect_epoch)

            #promedio de valores de acf en un electrodo en una epoca
            acf_mean_elect_all_epoch.append(np.mean(acf_elect_epoch))


            #calculo de acw_50 y acw_0 de sensor for both in lags and in seconds
            #recuerda que acw_50 y acw_0 son valores unicos, no como acf que es un conjunto de valores
            acw_50_lags_elect_epoch = np.argmax(acf_elect_epoch <= 0.5)
            acw_50_s_elect_epoch = acw_50_lags_elect_epoch / sfreq

            acw_50_elect_all_epoch.append(acw_50_s_elect_epoch)


            acw_0_lags_elect_epoch= np.argmax(acf_elect_epoch <= 0)
            acw_0_s_elect_epoch = acw_0_lags_elect_epoch / sfreq

            acw_0_elect_all_epoch.append(acw_0_s_elect_epoch)


        #APPEND valores de TODOS LOS ELECTODOS en TODAS LAS EPOCAS

        acf_elect_all_epoch_all.append(acf_elect_all_epoch)
        acf_mean_elect_all_epoch_all.append(acf_mean_elect_all_epoch)

        acw_50_elect_all_epoch_all.append(acw_50_elect_all_epoch)
        acw_0_elect_all_epoch_all.append(acw_0_elect_all_epoch)


       

    #promedio de valores de acw_50 y acw_0 en un electrodo para todas las epocas
    # acw_50_elect_all_epoch_mean = []
    # acw_0_elect_all_epoch_mean = []


    #promedio de los electrodos en todas las epocas
    # Convertir la lista de listas en un array de NumPy para cálculos más eficientes
    acw_50_elect_all_epoch_all_array = np.array(acw_50_elect_all_epoch_all)  # (21 filas, 59 columnas)
    acw_0_elect_all_epoch_all_array = np.array(acw_0_elect_all_epoch_all)  # (21 filas, 59 columnas)

    ##computo de la media de TODOS los electrodos en CADA EPOCA
    acw_50_elect_mean_epoch_all = np.mean(acw_50_elect_all_epoch_all_array, axis=1)
    acw_0_elect_mean_epoch_all = np.mean(acw_0_elect_all_epoch_all_array, axis=1)


    ##computo de la media de cada los electrodos en TODAS EPOCAS
    acw_50_elect_all_epoch_mean = np.mean(acw_50_elect_all_epoch_all_array, axis=0)       
    acw_0_elect_all_epoch_mean = np.mean(acw_0_elect_all_epoch_all_array, axis=0)
    

    # # Crear un DataFrame con las columnas necesarias

    table_autocorrelation = pd.DataFrame({
        'Subject': [subj] * num_conditions,  # Repite el sujeto para todas las filas
        'Condition': condition,  # Repite la combinación para todas las filas
        "Epoch": range(1, len(acf_elect_all_epoch_all) + 1),  # Número de épocas
        'acf_elect_all_epoch_all': acf_elect_all_epoch_all,
        "acf_mean_elect_all_epoch_all": acf_mean_elect_all_epoch_all,
        'acw_50_elect_all_epoch_all': acw_50_elect_all_epoch_all,
        'acw_0_elect_all_epoch_all': acw_0_elect_all_epoch_all,
        'acw_50_elect_mean_epoch_all': [acw_50_elect_mean_epoch_all] * len(acf_elect_all_epoch_all),
        'acw_0_elect_mean_epoch_all': [acw_0_elect_mean_epoch_all] * len(acf_elect_all_epoch_all),
        "acw_50_elect_all_epoch_mean": [acw_50_elect_all_epoch_mean] * len(acf_elect_all_epoch_all),
        "acw_0_elect_all_epoch_mean": [acw_0_elect_all_epoch_mean] * len(acf_elect_all_epoch_all)
        })

    #identificar acw_50


    #valores de estadística
        ## pero ver que valores son puto significativos de la ACF o de la ACW??



    isplot=False    

    # if isplot==True:
    #     # 1) Creamos un vector de lags en segundos,
    #     #    asumiendo que acf_val tiene tantos puntos como lags + 1.
    #     time_lags = np.arange(len(acf_val)) / sfreq

    #     # 2) Convertimos los índices (entero) de ACW_50 y ACW_0
    #     ACW_50_i = int(acw_50_lags)
    #     ACW_0_i = int(acw_0_lags)

    #     # 3) Figura
    #     plt.figure(figsize=(8, 4))

    #     # 4) Dibujamos la ACF en negro
    #     plt.plot(time_lags, acf_val, 'k', label='ACF')

    #     # 5) Acotamos el eje X a la duración total de la señal (o a lo que consideres)
    #     plt.xlim([0, time_lags[-1]])

    #     # 6) Rellenamos el área hasta ACW_50
    #     plt.fill_between(
    #         time_lags[:ACW_50_i + 1],
    #         acf_val[:ACW_50_i + 1],
    #         color='r', alpha=0.3, label='ACW-50 area'
    #     )

    #     # 7) Rellenamos el área hasta ACW_0
    #     plt.fill_between(
    #         time_lags[:ACW_0_i + 1],
    #         acf_val[:ACW_0_i + 1],
    #         color='m', alpha=0.3, label='ACW-0 area'
    #     )

    #     # 8) Título con valores de ACW
    #     plt.title(f'ACW-0 = {acw_0:.1f} s    ACW-50 = {acw_50:.1f} s')
    #     plt.xlabel('Lags (s)')
    #     plt.ylabel('Autocorrelation')
    #     plt.legend(loc='best')
    #     plt.show()

    return table_autocorrelation
    # return acf_epoch_all,acw_50_elect_all_epoch_all, acw_0_elect_all_epoch_all




In [5]:
table_autocorrelation= acf_epochs(epochs, isplot=False)

C:\Users\UCM\AppData\Local\Temp\ipykernel_13784\2254198396.py:11: FutureWarning: The current default of copy=False will change to copy=True in 1.7. Set the value of copy explicitly to avoid this warning
  data_epochs=epochs.copy().pick("eeg").get_data()


In [6]:
##codigo para agrupar todas las tablas

all_tables = []

for i in range(0,len(subject_names)):
    for h in range(0,len(combinaciones)):
        subj=subject_names[i]
        combinacion= combinaciones[h]
        path_epochs= fif_data / f"{subj}_epochs" / f"{subj}_{combinacion}-epo.fif"
        epochs = mne.read_epochs(path_epochs)
        table_autocorrelation= acf_epochs(epochs, isplot=False)
        all_tables.append(table_autocorrelation)

autocorrelation_subjects_all = pd.concat(all_tables, ignore_index=True)


Reading g:\PROYECTO_SELF\Data_self\fif_data\S01_epochs\S01_S1 - S4-epo.fif ...
    Found the data of interest:
        t =       0.00 ...    9198.00 ms
        0 CTF compensation matrices available
Not setting metadata
19 matching events found
No baseline correction applied
0 projection items activated


C:\Users\UCM\AppData\Local\Temp\ipykernel_13784\2254198396.py:11: FutureWarning: The current default of copy=False will change to copy=True in 1.7. Set the value of copy explicitly to avoid this warning
  data_epochs=epochs.copy().pick("eeg").get_data()


Reading g:\PROYECTO_SELF\Data_self\fif_data\S01_epochs\S01_S1 - S5-epo.fif ...
    Found the data of interest:
        t =       0.00 ...    9198.00 ms
        0 CTF compensation matrices available
Not setting metadata
21 matching events found
No baseline correction applied
0 projection items activated


C:\Users\UCM\AppData\Local\Temp\ipykernel_13784\2254198396.py:11: FutureWarning: The current default of copy=False will change to copy=True in 1.7. Set the value of copy explicitly to avoid this warning
  data_epochs=epochs.copy().pick("eeg").get_data()


Reading g:\PROYECTO_SELF\Data_self\fif_data\S01_epochs\S01_S2 - S4-epo.fif ...
    Found the data of interest:
        t =       0.00 ...    9198.00 ms
        0 CTF compensation matrices available
Not setting metadata
17 matching events found
No baseline correction applied
0 projection items activated


...

C:\Users\UCM\AppData\Local\Temp\ipykernel_13784\2254198396.py:11: FutureWarning: The current default of copy=False will change to copy=True in 1.7. Set the value of copy explicitly to avoid this warning
  data_epochs=epochs.copy().pick("eeg").get_data()


Reading g:\PROYECTO_SELF\Data_self\fif_data\S06_epochs\S06_S3 - S4-epo.fif ...
    Found the data of interest:
        t =       0.00 ...    9198.00 ms
        0 CTF compensation matrices available
Not setting metadata
23 matching events found
No baseline correction applied
0 projection items activated


C:\Users\UCM\AppData\Local\Temp\ipykernel_13784\2254198396.py:11: FutureWarning: The current default of copy=False will change to copy=True in 1.7. Set the value of copy explicitly to avoid this warning
  data_epochs=epochs.copy().pick("eeg").get_data()


Reading g:\PROYECTO_SELF\Data_self\fif_data\S06_epochs\S06_S3 - S5-epo.fif ...
    Found the data of interest:
        t =       0.00 ...    9198.00 ms
        0 CTF compensation matrices available
Not setting metadata
24 matching events found
No baseline correction applied
0 projection items activated


C:\Users\UCM\AppData\Local\Temp\ipykernel_13784\2254198396.py:11: FutureWarning: The current default of copy=False will change to copy=True in 1.7. Set the value of copy explicitly to avoid this warning
  data_epochs=epochs.copy().pick("eeg").get_data()


In [ ]:
autocorrelation_subjects_all

In [9]:
autocorrelation_subjects_all.to_pickle(acw_analysis_path / f"autocorrelation_subjects_all.pickle")

In [10]:
# Lista de variables a analizar
variables = [
    acf_elect_all_epoch_all,
    acf_mean_elect_all_epoch_all,
    acw_50_elect_all_epoch_all,
    acw_0_elect_all_epoch_all,
    acw_50_elect_mean_epoch_all,
    acw_0_elect_mean_epoch_all,
    acw_50_elect_all_epoch_mean,
    acw_0_elect_all_epoch_mean
]

# Lista de nombres para imprimir
variable_names = [
    "acf_elect_all_epoch_all",
    "acf_mean_elect_all_epoch_all",
    "acw_50_elect_all_epoch_all",
    "acw_0_elect_all_epoch_all",
    "acw_50_elect_mean_epoch_all",
    "acw_0_elect_mean_epoch_all",
    "acw_50_elect_all_epoch_mean",
    "acw_0_elect_all_epoch_mean"
]

# Bucle para imprimir los tipos y dimensiones
for var, name in zip(variables, variable_names):
    print(f"\n{name}:")
    print(f"  type({name}) is {type(var)}")
    
    try:
        print(f"  type({name}[0]) is {type(var[0])}")
        
        try:
            print(f"  type({name}[0][0]) is {type(var[0][0])}")
        except (IndexError, TypeError):
            print(f"  {name}[0] does not have a second dimension.")
            try:
                print(f"  type({name}[0][0][0]) is {type(var[0][0][0])}")
            except (IndexError, TypeError):
                print(f"  {name}[0][0] does not have a third dimension.")
    
    except (IndexError, TypeError):
        print(f"  {name} does not have a first dimension.")

NameError: name 'acf_elect_all_epoch_all' is not defined

# Lista de variables a analizar
variables = [
    acf_elect_all_epoch_all,
    acf_mean_elect_all_epoch_all,
    acw_50_elect_all_epoch_all,
    acw_0_elect_all_epoch_all,
    acw_50_elect_mean_epoch_all,
    acw_0_elect_mean_epoch_all,
    acw_50_elect_all_epoch_mean,
    acw_0_elect_all_epoch_mean
]

# Lista de nombres para imprimir
variable_names = [
    "acf_elect_all_epoch_all",
    "acf_mean_elect_all_epoch_all",
    "acw_50_elect_all_epoch_all",
    "acw_0_elect_all_epoch_all",
    "acw_50_elect_mean_epoch_all",
    "acw_0_elect_mean_epoch_all",
    "acw_50_elect_all_epoch_mean",
    "acw_0_elect_all_epoch_mean"
]

# Bucle para imprimir los tipos y dimensiones
for var, name in zip(variables, variable_names):
    print(f"\n{name}:")
    print(f"  type({name}) is {type(var)}")
    
    try:
        print(f"  type({name}[0]) is {type(var[0])}")
        
        try:
            print(f"  type({name}[0][0]) is {type(var[0][0])}")
        except (IndexError, TypeError):
            print(f"  {name}[0] does not have a second dimension.")
            try:
                print(f"  type({name}[0][0][0]) is {type(var[0][0][0])}")
            except (IndexError, TypeError):
                print(f"  {name}[0][0] does not have a third dimension.")
    
    except (IndexError, TypeError):
        print(f"  {name} does not have a first dimension.")

In [6]:

#import epochs object and get data ONLY ON MEG DATA
data_epochs=epochs.copy().pick("eeg").get_data()

#get duration
duration= epochs.tmax - epochs.tmin
#get sample frequency
sfreq= epochs.info['sfreq']
#get lags
lags=duration*sfreq


#list to store the values of acf, acw_50,acw_0 for each epoch for each sensor for each EPOCH
acf_elect_all_epoch_all = []
acf_mean_elect_all_epoch_all=[]

#conjunto de todos los valores de ACW_0-ACW_50 para cada sensor en cada epoca
acw_50_elect_all_epoch_all = []
acw_0_elect_all_epoch_all = []


#for each epoch
    
for j in range(0,len(data_epochs)):
    #take data for each epoch
    data_epoch=data_epochs[j]

    #list to store the values of acf, acw_50,acw_0 for each SENSOR for each EPOCH

    acf_elect_all_epoch = []
    
    acf_mean_elect_all_epoch = []

    acw_50_elect_all_epoch = []
    acw_0_elect_all_epoch = []




    #calculus of value  for EACH SENSOR
    for i in range(0,len(data_epoch)):
        #lags se puede dejar por defecto porque te cogelos valores
        #hasta los que tiene sentido calcularlo, aunque yo voy a calcularlo para todos los lags
        #calculo de acf de sensor
        #alfa lo dejo endefault que es la confianza del 95% 

        acf_elect_epoch, qstat_vals_elect_epoch, pvals_elect_epoch = acf(
            data_epoch[i],
            qstat=True,
            nlags=lags,
        )

        #conjunto de valores de acf en un electrodo en una epoca
        acf_elect_all_epoch.append(acf_elect_epoch)

        #promedio de valores de acf en un electrodo en una epoca
        acf_mean_elect_all_epoch.append(np.mean(acf_elect_epoch))


        #calculo de acw_50 y acw_0 de sensor for both in lags and in seconds
        #recuerda que acw_50 y acw_0 son valores unicos, no como acf que es un conjunto de valores
        acw_50_lags_elect_epoch = np.argmax(acf_elect_epoch <= 0.5)
        acw_50_s_elect_epoch = acw_50_lags_elect_epoch / sfreq

        acw_50_elect_all_epoch.append(acw_50_s_elect_epoch)


        acw_0_lags_elect_epoch= np.argmax(acf_elect_epoch <= 0)
        acw_0_s_elect_epoch = acw_0_lags_elect_epoch / sfreq

        acw_0_elect_all_epoch.append(acw_0_s_elect_epoch)


    #APPEND valores de TODOS LOS ELECTODOS en TODAS LAS EPOCAS

    acf_elect_all_epoch_all.append(acf_elect_all_epoch)
    acf_mean_elect_all_epoch_all.append(acf_mean_elect_all_epoch)

    acw_50_elect_all_epoch_all.append(acw_50_elect_all_epoch)
    acw_0_elect_all_epoch_all.append(acw_0_elect_all_epoch)


    

#promedio de valores de acw_50 y acw_0 en un electrodo para todas las epocas
# acw_50_elect_all_epoch_mean = []
# acw_0_elect_all_epoch_mean = []


#promedio de los electrodos en todas las epocas
# Convertir la lista de listas en un array de NumPy para cálculos más eficientes
acw_50_elect_all_epoch_all_array = np.array(acw_50_elect_all_epoch_all)  # (21 filas, 59 columnas)
acw_0_elect_all_epoch_all_array = np.array(acw_0_elect_all_epoch_all)  # (21 filas, 59 columnas)

##computo de la media de TODOS los electrodos en CADA EPOCA
acw_50_elect_mean_epoch_all = np.mean(acw_50_elect_all_epoch_all_array, axis=1)
acw_0_elect_mean_epoch_all = np.mean(acw_0_elect_all_epoch_all_array, axis=1)


##computo de la media de cada los electrodos en TODAS EPOCAS
acw_50_elect_all_epoch_mean = np.mean(acw_50_elect_all_epoch_all_array, axis=0)       
acw_0_elect_all_epoch_mean = np.mean(acw_0_elect_all_epoch_all_array, axis=0)



num_epochs=len(data_epochs)
num_elects=len(data_epoch)

shape_tabla=num_epochs*num_elects

acf_elect_all_epoch_all_list = np.array(acf_elect_all_epoch_all).reshape(num_epochs * num_elects, 4600).tolist()

table_autocorrelation = pd.DataFrame({
    'Subject': [subj] * shape_tabla,  # Repite el sujeto para todas las filas
    'Condition': [condition] * shape_tabla,  # Repite la condición para todas las filas
    "Epoch": np.repeat(np.arange(num_epochs), num_elects),  # Repite épocas
    "Elect": np.tile(np.arange(num_elects), num_epochs),  # Número de electrodos
    "acf_elect_all_epoch_all": acf_elect_all_epoch_all_list,  # Convierte la tercera dimensión en listas
    "acw_50_elect_all_epoch_all": np.array(acw_50_elect_all_epoch_all).flatten(),
    "acw_0_elect_all_epoch_all": np.array(acw_0_elect_all_epoch_all).flatten()
})

C:\Users\UCM\AppData\Local\Temp\ipykernel_15620\3978060343.py:2: FutureWarning: The current default of copy=False will change to copy=True in 1.7. Set the value of copy explicitly to avoid this warning
  data_epochs=epochs.copy().pick("eeg").get_data()


In [5]:
condition=combinacion

In [ ]:
table_autocorrelation

Subject Condition  Epoch  Elect  \
0        S01   S1 - S4      0      0   
1        S01   S1 - S4      0      1   
2        S01   S1 - S4      0      2   
3        S01   S1 - S4      0      3   
4        S01   S1 - S4      0      4   
...      ...       ...    ...    ...   
1234     S01   S1 - S4     20     54   
1235     S01   S1 - S4     20     55   
1236     S01   S1 - S4     20     56   
1237     S01   S1 - S4     20     57   
1238     S01   S1 - S4     20     58   

                                acf_elect_all_epoch_all  \
0     [1.0, 0.9688171127433391, 0.8953624983349072, ...   
1     [1.0, 0.9665382526051076, 0.8874305555006822, ...   
2     [1.0, 0.9671703247954537, 0.889051256146879, 0...   
3     [1.0, 0.9760178302319968, 0.9201873920582854, ...   
4     [1.0, 0.9868794301034245, 0.9554757778916378, ...   
...                                                 ...   
1234  [1.0, 0.9941151566901699, 0.9787819567963149, ...   
1235  [1.0, 0.9919158611575877, 0.970666360128749, 0...   
1236  [1.0, 0.9858840724718368, 0.9523003641161032, ...   
1237  [1.0, 0.9880524484486692, 0.959296629396974, 0...   
1238  [1.0, 0.9907858997901391, 0.9677286454619359, ...   

      acw_50_elect_all_epoch_all  acw_0_elect_all_epoch_all  
0                          0.022                      0.522  
1                          0.020                      0.684  
2                          0.018                      0.506  
3                          0.036                      0.898  
4                          0.056                      1.762  
...                          ...                        ...  
1234                       0.042                      0.650  
1235                       0.030                      0.614  
1236                       0.042                      0.530  
1237                       0.118                      0.550  
1238                       0.038                      0.612  

[1239 rows x 7 columns]

In [8]:
acw_0_elect_all_epoch_all

[[np.float64(0.522),
  np.float64(0.684),
  np.float64(0.506),
  np.float64(0.898),
  np.float64(1.762),
  np.float64(1.13),
  np.float64(0.496),
  np.float64(0.904),
  np.float64(0.9),
  np.float64(1.358),
  np.float64(1.504),
  np.float64(1.498),
  np.float64(1.116),
  np.float64(1.104),
  np.float64(1.076),
  np.float64(0.512),
  np.float64(0.626),
  np.float64(1.454),
  np.float64(1.496),
  np.float64(1.492),
  np.float64(1.754),
  np.float64(1.718),
  np.float64(1.706),
  np.float64(0.654),
  np.float64(0.524),
  np.float64(1.006),
  np.float64(1.546),
  np.float64(1.482),
  np.float64(1.35),
  np.float64(1.492),
  np.float64(1.754),
  np.float64(1.76),
  np.float64(1.176),
  np.float64(1.692),
  np.float64(2.352),
  np.float64(1.502),
  np.float64(1.5),
  np.float64(1.208),
  np.float64(1.698),
  np.float64(2.022),
  np.float64(2.462),
  np.float64(1.93),
  np.float64(0.14),
  np.float64(1.066),
  np.float64(1.968),
  np.float64(2.046),
  np.float64(2.03),
  np.float64(2.092),
  